In [1]:
import pandas as pd
import sys
import numpy as np
from tqdm import tqdm
from copy import deepcopy

In [2]:
sys.path.append('D:\\ML\\Kis_Api_test')

In [3]:
from BackTesting_System.backtesting import BackTesting, Utils

In [4]:
bt1 = BackTesting()
ut = Utils()

In [5]:
df = pd.read_csv('../../../result.csv')

In [54]:
df_test = df[(df['종목명'] == '삼성전자')] #| (df['종목명'] == 'POSCO홀딩스')]

In [55]:
#method 1: fractal candlestick pattern
# determine bullish fractal 
def is_support(df,i):  
    cond1 = df['최저가'][i] < df['최저가'][i-1]   
    cond2 = df['최저가'][i] < df['최저가'][i+1]   
    cond3 = df['최저가'][i+1] < df['최저가'][i+2]   
    cond4 = df['최저가'][i-1] < df['최저가'][i-2]  
    return (cond1 and cond2 and cond3 and cond4) 

# determine bearish fractal
def is_resistance(df,i):  
    cond1 = df['최고가'][i] > df['최고가'][i-1]   
    cond2 = df['최고가'][i] > df['최고가'][i+1]   
    cond3 = df['최고가'][i+1] > df['최고가'][i+2]   
    cond4 = df['최고가'][i-1] > df['최고가'][i-2]  
    return (cond1 and cond2 and cond3 and cond4)

# to make sure the new level area does not exist already
def is_far_from_level(value, levels, df):    
    ave =  np.mean(df['최고가'] - df['최저가'])    
    return np.sum([abs(value-level)<ave for _,level in levels])==0

In [56]:
def make_df(df_raw):
    levels = []
    object_list = df_raw['코드'].unique()
    for i in tqdm(object_list):
        idx = df_raw[df_raw['코드']==i].index
        for i in idx[2:-2]:
            if is_support(df_raw, i):
                low = df['최저가'][i]
                if is_far_from_level(low, levels, df_raw):
                    levels.append((i,low))
            elif is_resistance(df_raw,i):
                high = df['최고가'][i]
                if is_far_from_level(high,levels, df_raw):
                    levels.append((i,high))
    return levels

In [57]:
levels = make_df(df_test)

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00,  6.63it/s]


In [58]:
levels.insert(0, (df_test.index[0], 0))

In [59]:
levels

[(817838, 0),
 (817851, 49800),
 (817860, 45080),
 (817868, 52020),
 (817882, 46920),
 (817983, 48450),
 (818018, 40400),
 (818065, 36850),
 (818141, 43800),
 (818271, 53500),
 (818302, 57300),
 (818329, 55200),
 (818339, 62000),
 (818452, 60400),
 (818504, 59000),
 (818526, 67000),
 (818531, 69500),
 (818562, 96800),
 (818572, 89900),
 (818580, 82100),
 (818586, 86000),
 (818646, 78400),
 (818648, 80900),
 (818705, 83300),
 (818718, 76600),
 (818720, 73800),
 (818744, 71200),
 (818748, 68300),
 (818812, 79600),
 (818883, 64500),
 (819030, 63200)]

In [60]:
levels_copy = deepcopy(levels)[::-1]
df_test['지지저항'] = 0

C:\Users\SCH\AppData\Local\Temp\ipykernel_8224\1064177164.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [61]:
for idx, row in tqdm(df_test.iterrows()):
    print(idx, levels_copy[-1])
    if idx > levels_copy[-1][0]:
        levels_copy.pop()
    df_test.loc[idx, '지지저항'] = levels_copy[-1][1]
        

480it [00:00, 4717.68it/s]

817838 (817838, 0)
817839 (817838, 0)
817840 (817851, 49800)
817841 (817851, 49800)
817842 (817851, 49800)
817843 (817851, 49800)
817844 (817851, 49800)
817845 (817851, 49800)
817846 (817851, 49800)
817847 (817851, 49800)
817848 (817851, 49800)
817849 (817851, 49800)
817850 (817851, 49800)
817851 (817851, 49800)
817852 (817851, 49800)
817853 (817860, 45080)
817854 (817860, 45080)
817855 (817860, 45080)
817856 (817860, 45080)
817857 (817860, 45080)
817858 (817860, 45080)
817859 (817860, 45080)
817860 (817860, 45080)
817861 (817860, 45080)
817862 (817868, 52020)
817863 (817868, 52020)
817864 (817868, 52020)
817865 (817868, 52020)
817866 (817868, 52020)
817867 (817868, 52020)
817868 (817868, 52020)
817869 (817868, 52020)
817870 (817882, 46920)
817871 (817882, 46920)
817872 (817882, 46920)
817873 (817882, 46920)
817874 (817882, 46920)
817875 (817882, 46920)
817876 (817882, 46920)
817877 (817882, 46920)
817878 (817882, 46920)
817879 (817882, 46920)
817880 (817882, 46920)
817881 (817882, 469

1193it [00:00, 4943.49it/s]

818872 (818883, 64500)
818873 (818883, 64500)
818874 (818883, 64500)
818875 (818883, 64500)
818876 (818883, 64500)
818877 (818883, 64500)
818878 (818883, 64500)
818879 (818883, 64500)
818880 (818883, 64500)
818881 (818883, 64500)
818882 (818883, 64500)
818883 (818883, 64500)
818884 (818883, 64500)
818885 (819030, 63200)
818886 (819030, 63200)
818887 (819030, 63200)
818888 (819030, 63200)
818889 (819030, 63200)
818890 (819030, 63200)
818891 (819030, 63200)
818892 (819030, 63200)
818893 (819030, 63200)
818894 (819030, 63200)
818895 (819030, 63200)
818896 (819030, 63200)
818897 (819030, 63200)
818898 (819030, 63200)
818899 (819030, 63200)
818900 (819030, 63200)
818901 (819030, 63200)
818902 (819030, 63200)
818903 (819030, 63200)
818904 (819030, 63200)
818905 (819030, 63200)
818906 (819030, 63200)
818907 (819030, 63200)
818908 (819030, 63200)
818909 (819030, 63200)
818910 (819030, 63200)
818911 (819030, 63200)
818912 (819030, 63200)
818913 (819030, 63200)
818914 (819030, 63200)
818915 (819

IndexError: list index out of range

In [62]:
df_test.iloc[1144:, -1] = 72000

In [63]:
import plotly.graph_objects as go
def making_mt_plot( handle_data: 'pd.DataFrame',
                    code: 'str',
                    jounal: 'pd.DataFrame' = None):
    '''data plotting'''
    code = int(code)
    handle_data_copy = deepcopy(handle_data) 
    hd = handle_data_copy[handle_data_copy['코드'] == code]
    if jounal is not None:
        jounal_copy = deepcopy(jounal)
#         dates = self.deduplication_dates(code=code, jounal=jounal_copy)
    # hd['날짜'] = hd['날짜'].apply(lambda x : datetime.strftime(x, '%Y-%m-%d'))  #for DB structure
    fig = go.Figure()
    fig.add_trace(go.Candlestick(x=hd['날짜'], 
                            open=hd['시가'],
                            high=hd['최고가'],
                            low=hd['최저가'],
                            close=hd['종가']))
    fig.add_trace(go.Scatter(x=hd['날짜'], y=hd['지지저항']))
    fig.layout = dict(title='종목명: ' + str(hd['종목명'].unique()) + '  |  코드: ' + str(code), 
                    xaxis = dict(type="category", 
                    categoryorder='category ascending'))
    fig.update_xaxes(nticks=5)
    fig.update_layout(width=1000, height=500)
#     for buy_date, sell_date in dates:
#         print(buy_date, sell_date)
#         fig.add_vrect(x0=buy_date, x1=sell_date, 
#                     fillcolor="gray", opacity=0.25, line_width=0)
    return fig

In [66]:
making_mt_plot(df_test, '5930')

In [70]:
df_test[df_test['종목명']=='삼성전자'].head(20)

Unnamed: 0          날짜     종가     시가    최고가    최저가     누적거래량  \
817838      817838  2018-01-29  51220  51200  51480  50900  11838800   
817839      817839  2018-01-30  49800  50440  50640  49780  12284550   
817840      817840  2018-01-31  49900  50020  54140  49600  64681300   
817841      817841  2018-02-01  49820  50620  50960  49720  27609450   
817842      817842  2018-02-02  47700  49380  49400  47700  29260350   
817843      817843  2018-02-05  47920  46500  48320  46000  28357900   
817844      817844  2018-02-06  47420  46600  47920  46580  19406450   
817845      817845  2018-02-07  45800  48240  48260  45800  23448050   
817846      817846  2018-02-08  46000  46120  46620  45980  23251050   
817847      817847  2018-02-09  44700  44440  45180  44420  17465000   
817848      817848  2018-02-12  45720  45100  46320  45040  15754950   
817849      817849  2018-02-13  47540  46200  48060  46200  18923250   
817850      817850  2018-02-14  49000  48080  49100  47940  18905900   
817851      817851  2018-02-19  48380  49800  49800  47860  15353450   
817852      817852  2018-02-20  47400  48040  48160  47220  10122600   
817853      817853  2018-02-21  47280  47280  47580  46840  12880200   
817854      817854  2018-02-22  46760  47260  47260  46760   8869950   
817855      817855  2018-02-23  47220  46760  47800  46760  12423300   
817856      817856  2018-02-26  47380  47280  47560  47080   9560650   
817857      817857  2018-02-27  47380  48360  48380  47380   9830550   

               누적거래대금   종목명       5_mom      10_mom  20_mom    buy   sell  \
817838   606585731237  삼성전자         NaN         NaN     NaN  False  False   
817839   616153770244  삼성전자         NaN         NaN     NaN  False  False   
817840  3351453496000  삼성전자         NaN         NaN     NaN  False  False   
817841  1385573101302  삼성전자         NaN         NaN     NaN  False  False   
817842  1408721416002  삼성전자         NaN         NaN     NaN  False  False   
817843  1333662855850  삼성전자   93.557204         NaN     NaN  False  False   
817844   913939877925  삼성전자   95.220884         NaN     NaN  False  False   
817845  1097890924000  삼성전자   91.783567         NaN     NaN  False  False   
817846  1075498203230  삼성전자   92.332397         NaN     NaN  False  False   
817847   780790538640  삼성전자   93.710692         NaN     NaN  False  False   
817848   719931323000  삼성전자   95.409015   89.262007     NaN  False  False   
817849   896530740450  삼성전자  100.253058   95.461847     NaN  False  False   
817850   922638233330  삼성전자  106.986900   98.196393     NaN   True  False   
817851   746462578640  삼성전자  105.173913   97.109595     NaN  False  False   
817852   481057664650  삼성전자  106.040268   99.371069     NaN  False  False   
817853   607522785000  삼성전자  103.412073   98.664441     NaN  False  False   
817854   416552606000  삼성전자   98.359276   98.608182     NaN  False  False   
817855   587288884490  삼성전자   96.367347  103.100437     NaN  False   True   
817856   452021608155  삼성전자   97.933030  103.000000     NaN  False  False   
817857   470190818669  삼성전자   99.957806  105.995526     NaN  False  False   

        구매수량    코드         상장일   지지저항  
817838     3  5930  1975-06-11      0  
817839     3  5930  1975-06-11  49800  
817840     3  5930  1975-06-11  49800  
817841     3  5930  1975-06-11  49800  
817842     3  5930  1975-06-11  49800  
817843     3  5930  1975-06-11  49800  
817844     3  5930  1975-06-11  49800  
817845     3  5930  1975-06-11  49800  
817846     3  5930  1975-06-11  49800  
817847     3  5930  1975-06-11  49800  
817848     3  5930  1975-06-11  49800  
817849     3  5930  1975-06-11  49800  
817850     3  5930  1975-06-11  49800  
817851     3  5930  1975-06-11  49800  
817852     3  5930  1975-06-11  45080  
817853     3  5930  1975-06-11  45080  
817854     3  5930  1975-06-11  45080  
817855     3  5930  1975-06-11  45080  
817856     3  5930  1975-06-11  45080  
817857     3  5930  1975-06-11  45080

In [88]:
df[df['종목명'] == 'POSCO홀딩스'][['코드', '지지저항']]

코드    지지저항
637101  5490  768000
637102  5490  768000
637103  5490  768000
637104  5490  768000
637105  5490  768000
...      ...     ...
638309  5490  768000
638310  5490  768000
638311  5490  768000
638312  5490  768000
638313  5490  768000

[1213 rows x 2 columns]

In [14]:
df_test1[df_test1['buy'] == True]

Unnamed: 0          날짜    종가     시가    최고가   최저가    누적거래량  \
6                6  2022-11-28  7420  10200  10450  7420  3458712   
7                7  2022-11-29  6900   7330   7350  6860   834344   
8                8  2022-11-30  6360   6960   7010  6340   855296   
9                9  2022-12-01  6330   6470   6530  6320   431925   
10              10  2022-12-02  6280   6330   6480  6280   306045   
...            ...         ...   ...    ...    ...   ...      ...   
882122      882122  2022-12-23  3795   3885   3930  3755    50452   
882123      882123  2022-12-26  3785   3795   3800  3650    75667   
882124      882124  2022-12-27  3810   3750   3840  3750    30791   
882125      882125  2022-12-28  3890   3800   3930  3770    14512   
882126      882126  2022-12-29  3895   3855   3925  3695    35383   

             누적거래대금       종목명       5_mom     10_mom     20_mom   buy   sell  \
6       27586626590  유니드비티플러스         NaN        NaN        NaN  True  False   
7        5849468050  유니드비티플러스         NaN        NaN        NaN  True  False   
8        5697738920  유니드비티플러스         NaN        NaN        NaN  True  False   
9        2764739060  유니드비티플러스         NaN        NaN        NaN  True  False   
10       1945031730  유니드비티플러스         NaN        NaN        NaN  True  False   
...             ...       ...         ...        ...        ...   ...    ...   
882122    191959725  한진중공업홀딩스   96.687898  95.591940  90.572792  True  False   
882123    282358160  한진중공업홀딩스   96.188056  94.862155  95.100503  True  False   
882124    116935765  한진중공업홀딩스   97.442455  95.250000  93.268054  True  False   
882125     55566740  한진중공업홀딩스  101.302083  96.526055  92.840095  True  False   
882126    134048100  한진중공업홀딩스  100.257400  98.110831  93.629808  True  False   

        구매수량      코드         상장일  20_low  
6          3  446070  2022-11-28  8030.0  
7          3  446070  2022-11-28  8030.0  
8          3  446070  2022-11-28  8030.0  
9          3  446070  2022-11-28  8030.0  
10         3  446070  2022-11-28  8030.0  
...      ...     ...         ...     ...  
882122     3  003480  1956-03-03  2050.0  
882123     3  003480  1956-03-03  2050.0  
882124     3  003480  1956-03-03  2050.0  
882125     3  003480  1956-03-03  2050.0  
882126     3  003480  1956-03-03  2050.0  

[882121 rows x 18 columns]

In [13]:
df_test1.shape

(882127, 18)

In [6]:
def make_signal(df):
    object_list = df['종목명'].unique()
    for i in object_list:
        idx = df[df['종목명']==i].index
        df.loc[idx[0]:idx[-1],'20_low']= df.loc[idx[0]:idx[-1], '최저가'].shift(-20).min()
        con1 = df['종가'] <= df['20_low']*0.01
        con2 = df['종가'] >= df['20_low']*-0.01
        df['buy'] = con1|con2
        con3 = df['종가'] <= df['20_low']*-0.05
        df['sell'] = con3
    return df

In [7]:
df_test1 = make_signal(df)

In [8]:
df_test1['코드'] = df_test1['코드'].apply(lambda x: str(x).zfill(6))

In [21]:
bt1.MONEY = 9990000000

In [22]:
bt1.buy_sell(df=df_test1, buy='buy', sell='sell')

('2018-01-29', True, False)
['2018-01-29', '108320', 53600, 3, 226.0, '매수']
['2018-01-29', '178920', 42850, 3, 181.0, '매수']
['2018-01-29', '097520', 17300, 3, 73.0, '매수']
['2018-01-29', '036420', 66373, 3, 280.0, '매수']
['2018-01-29', '003670', 47493, 3, 200.0, '매수']
['2018-01-29', '192080', 61400, 3, 259.0, '매수']
['2018-01-29', '068270', 286023, 3, 1206.0, '매수']
['2018-01-29', '284740', 39900, 3, 168.0, '매수']
['2018-01-29', '285130', 74726, 3, 315.0, '매수']
['2018-01-29', '282330', 227000, 3, 957.0, '매수']
['2018-01-29', '092780', 4600, 3, 19.0, '매수']
['2018-01-29', '272450', 26840, 3, 113.0, '매수']
['2018-01-29', '281820', 20750, 3, 87.0, '매수']
['2018-01-29', '282690', 13600, 3, 57.0, '매수']
['2018-01-29', '272550', 24650, 3, 104.0, '매수']
['2018-01-29', '055490', 29150, 3, 123.0, '매수']
['2018-01-29', '280360', 173500, 3, 731.0, '매수']
['2018-01-29', '271980', 50666, 3, 214.0, '매수']
['2018-01-29', '035720', 27899, 3, 118.0, '매수']
['2018-01-29', '271560', 119000, 3, 502.0, '매수']
['2018-01-29

['2018-01-29', '001560', 5840, 3, 25.0, '매수']
['2018-01-29', '079430', 29750, 3, 125.0, '매수']
['2018-01-29', '084010', 10500, 3, 44.0, '매수']
['2018-01-29', '075180', 7200, 3, 30.0, '매수']
['2018-01-29', '083420', 3683, 3, 16.0, '매수']
['2018-01-29', '084690', 10300, 3, 43.0, '매수']
['2018-01-29', '071950', 1225, 3, 5.0, '매수']
['2018-01-29', '084680', 1855, 3, 8.0, '매수']
['2018-01-29', '084670', 26952, 3, 114.0, '매수']
['2018-01-29', '042700', 6175, 3, 26.0, '매수']
['2018-01-29', '004890', 79500, 3, 335.0, '매수']
['2018-01-29', '010960', 4690, 3, 20.0, '매수']
['2018-01-29', '073240', 5970, 3, 25.0, '매수']
['2018-01-29', '081000', 32045, 3, 135.0, '매수']
['2018-01-29', '014830', 57618, 3, 243.0, '매수']
['2018-01-29', '041650', 8020, 3, 34.0, '매수']
['2018-01-29', '023810', 4850, 3, 20.0, '매수']
['2018-01-29', '078930', 70700, 3, 298.0, '매수']
['2018-01-29', '077500', 10600, 3, 45.0, '매수']
['2018-01-29', '058730', 7000, 3, 30.0, '매수']
['2018-01-29', '034220', 33050, 3, 139.0, '매수']
['2018-01-29', '078

['2018-01-29', '002100', 6070, 3, 26.0, '매수']
['2018-01-29', '004870', 4902, 3, 21.0, '매수']
['2018-01-29', '007590', 7250, 3, 31.0, '매수']
['2018-01-29', '004430', 24800, 3, 105.0, '매수']
['2018-01-29', '002780', 2140, 3, 9.0, '매수']
['2018-01-29', '000650', 91500, 3, 386.0, '매수']
['2018-01-29', '000430', 4740, 3, 20.0, '매수']
['2018-01-29', '001080', 18600, 3, 78.0, '매수']
['2018-01-29', '004700', 40250, 3, 170.0, '매수']
['2018-01-29', '004360', 13400, 3, 56.0, '매수']
['2018-01-29', '008970', 864, 3, 4.0, '매수']
['2018-01-29', '002880', 1085, 3, 5.0, '매수']
['2018-01-29', '001260', 6480, 3, 27.0, '매수']
['2018-01-29', '005800', 14500, 3, 61.0, '매수']
['2018-01-29', '002630', 2868, 3, 12.0, '매수']
['2018-01-29', '001550', 12850, 3, 54.0, '매수']
['2018-01-29', '005430', 53500, 3, 226.0, '매수']
['2018-01-29', '004910', 10350, 3, 44.0, '매수']
['2018-01-29', '004690', 121500, 3, 512.0, '매수']
['2018-01-29', '003080', 6060, 3, 26.0, '매수']
['2018-01-29', '002600', 247500, 3, 1043.0, '매수']
['2018-01-29', '00

['2018-01-30', '036570', 442500, 3, 1865.0, '매수']
['2018-01-30', '071090', 2310, 3, 10.0, '매수']
['2018-01-30', '069730', 6190, 3, 26.0, '매수']
['2018-01-30', '006890', 4885, 3, 21.0, '매수']
['2018-01-30', '011500', 4495, 3, 19.0, '매수']
['2018-01-30', '069960', 103500, 3, 436.0, '매수']
['2018-01-30', '069460', 950, 3, 4.0, '매수']
['2018-01-30', '069620', 185000, 3, 780.0, '매수']
['2018-01-30', '027740', 3187, 3, 13.0, '매수']
['2018-01-30', '036530', 15350, 3, 65.0, '매수']
['2018-01-30', '033530', 9080, 3, 38.0, '매수']
['2018-01-30', '058430', 31250, 3, 132.0, '매수']
['2018-01-30', '068290', 11150, 3, 47.0, '매수']
['2018-01-30', '030610', 12000, 3, 51.0, '매수']
['2018-01-30', '009240', 169000, 3, 712.0, '매수']
['2018-01-30', '034300', 31450, 3, 133.0, '매수']
['2018-01-30', '017370', 9320, 3, 39.0, '매수']
['2018-01-30', '066570', 101000, 3, 426.0, '매수']
['2018-01-30', '024720', 50800, 3, 214.0, '매수']
['2018-01-30', '064960', 48950, 3, 206.0, '매수']
['2018-01-30', '037710', 48600, 3, 205.0, '매수']
['2018-

['2018-01-31', '009540', 139000, 3, 586.0, '매수']
['2018-01-31', '024090', 12600, 3, 53.0, '매수']
['2018-01-31', '006840', 85500, 3, 360.0, '매수']
['2018-01-31', '006650', 331500, 3, 1398.0, '매수']
['2018-01-31', '035150', 7160, 3, 30.0, '매수']
['2018-01-31', '035000', 9440, 3, 40.0, '매수']
['2018-01-31', '033250', 922, 3, 4.0, '매수']
['2018-01-31', '033240', 25900, 3, 109.0, '매수']
['2018-01-31', '030000', 21250, 3, 90.0, '매수']
['2018-01-31', '026890', 6150, 3, 26.0, '매수']
['2018-01-31', '029460', 20800, 3, 88.0, '매수']
['2018-01-31', '024890', 2780, 3, 12.0, '매수']
['2018-01-31', '017940', 59300, 3, 250.0, '매수']
['2018-01-31', '018670', 104169, 3, 439.0, '매수']
['2018-01-31', '023590', 25050, 3, 106.0, '매수']
['2018-01-31', '014440', 5040, 3, 21.0, '매수']
['2018-01-31', '011790', 45300, 3, 191.0, '매수']
['2018-01-31', '010600', 3235, 3, 14.0, '매수']
['2018-01-31', '025890', 2455, 3, 10.0, '매수']
['2018-01-31', '024900', 1625, 3, 7.0, '매수']
['2018-01-31', '023960', 1787, 3, 8.0, '매수']
['2018-01-31', 

...

['2018-07-13', '004710', 9099, 3, 38.0, '매수']
['2018-07-13', '016610', 4000, 3, 17.0, '매수']
['2018-07-13', '008930', 62952, 3, 265.0, '매수']
['2018-07-13', '005500', 46900, 3, 198.0, '매수']
['2018-07-13', '005490', 316500, 3, 1334.0, '매수']
['2018-07-13', '002410', 1820, 3, 8.0, '매수']
['2018-07-13', '005690', 16450, 3, 69.0, '매수']
['2018-07-13', '001230', 7450, 3, 31.0, '매수']
['2018-07-13', '006340', 1770, 3, 7.0, '매수']
['2018-07-13', '005950', 10102, 3, 43.0, '매수']
['2018-07-13', '016360', 33350, 3, 141.0, '매수']
['2018-07-13', '002810', 14195, 3, 60.0, '매수']
['2018-07-13', '001750', 7290, 3, 31.0, '매수']
['2018-07-13', '003470', 3685, 3, 16.0, '매수']
['2018-07-13', '002620', 25650, 3, 108.0, '매수']
['2018-07-13', '015260', 4994, 3, 21.0, '매수']
['2018-07-13', '009460', 984, 3, 4.0, '매수']
['2018-07-13', '005720', 6320, 3, 27.0, '매수']
['2018-07-13', '006660', 10850, 3, 46.0, '매수']
['2018-07-13', '004490', 31650, 3, 133.0, '매수']
['2018-07-13', '011000', 3339, 3, 14.0, '매수']
['2018-07-13', '0093

['2018-07-13', '003090', 17250, 3, 73.0, '매수']
['2018-07-13', '003780', 3055, 3, 13.0, '매수']
['2018-07-13', '003520', 7470, 3, 31.0, '매수']
['2018-07-13', '003200', 116000, 3, 489.0, '매수']
['2018-07-13', '006220', 5774, 3, 24.0, '매수']
['2018-07-13', '004150', 4986, 3, 21.0, '매수']
['2018-07-13', '007210', 3305, 3, 14.0, '매수']
['2018-07-13', '000400', 2695, 3, 11.0, '매수']
['2018-07-13', '001130', 179000, 3, 755.0, '매수']
['2018-07-13', '001680', 26600, 3, 112.0, '매수']
['2018-07-13', '003550', 68677, 3, 290.0, '매수']
['2018-07-13', '000640', 99900, 3, 421.0, '매수']
['2018-07-13', '003690', 9403, 3, 40.0, '매수']
['2018-07-13', '003300', 16877, 3, 71.0, '매수']
['2018-07-13', '003030', 59252, 3, 250.0, '매수']
['2018-07-13', '001440', 1165, 3, 5.0, '매수']
['2018-07-13', '001790', 2415, 3, 10.0, '매수']
['2018-07-13', '000070', 111500, 3, 470.0, '매수']
['2018-07-13', '002420', 16253, 3, 69.0, '매수']
['2018-07-13', '000240', 18000, 3, 76.0, '매수']
['2018-07-13', '000950', 22600, 3, 95.0, '매수']
['2018-07-13'

('2019-07-25', True, False)
('2019-07-26', True, False)
('2019-07-29', True, False)
('2019-07-30', True, False)
('2019-07-31', True, False)
('2019-08-01', True, False)
('2019-08-02', True, False)
('2019-08-05', True, False)
('2019-08-06', True, False)
('2019-08-07', True, False)
('2019-08-08', True, False)
('2019-08-09', True, False)
('2019-08-12', True, False)
('2019-08-13', True, False)
('2019-08-14', True, False)
('2019-08-16', True, False)
('2019-08-19', True, False)
('2019-08-20', True, False)
('2019-08-21', True, False)
('2019-08-22', True, False)
('2019-08-23', True, False)
('2019-08-26', True, False)
('2019-08-27', True, False)
('2019-08-28', True, False)
('2019-08-29', True, False)
('2019-08-30', True, False)
('2019-09-02', True, False)
('2019-09-03', True, False)
('2019-09-04', True, False)
('2019-09-05', True, False)
('2019-09-06', True, False)
('2019-09-09', True, False)
('2019-09-10', True, False)
('2019-09-11', True, False)
('2019-09-16', True, False)
('2019-09-17', True,

('2020-10-12', True, False)
('2020-10-13', True, False)
('2020-10-14', True, False)
('2020-10-15', True, False)
('2020-10-16', True, False)
('2020-10-19', True, False)
('2020-10-20', True, False)
('2020-10-21', True, False)
('2020-10-22', True, False)
('2020-10-23', True, False)
('2020-10-26', True, False)
('2020-10-27', True, False)
('2020-10-28', True, False)
('2020-10-29', True, False)
('2020-10-30', True, False)
('2020-11-02', True, False)
('2020-11-03', True, False)
('2020-11-04', True, False)
('2020-11-05', True, False)
('2020-11-06', True, False)
('2020-11-09', True, False)
('2020-11-10', True, False)
('2020-11-11', True, False)
('2020-11-12', True, False)
('2020-11-13', True, False)
('2020-11-16', True, False)
('2020-11-17', True, False)
('2020-11-18', True, False)
('2020-11-19', True, False)
('2020-11-20', True, False)
('2020-11-23', True, False)
('2020-11-24', True, False)
('2020-11-25', True, False)
('2020-11-26', True, False)
('2020-11-27', True, False)
('2020-11-30', True,

('2021-12-15', True, False)
('2021-12-16', True, False)
('2021-12-17', True, False)
('2021-12-20', True, False)
('2021-12-21', True, False)
('2021-12-22', True, False)
('2021-12-23', True, False)
('2021-12-24', True, False)
('2021-12-27', True, False)
('2021-12-28', True, False)
('2021-12-29', True, False)
('2021-12-30', True, False)
('2022-01-03', True, False)
('2022-01-04', True, False)
('2022-01-05', True, False)
('2022-01-06', True, False)
('2022-01-07', True, False)
('2022-01-10', True, False)
('2022-01-11', True, False)
('2022-01-12', True, False)
('2022-01-13', True, False)
('2022-01-14', True, False)
('2022-01-17', True, False)
('2022-01-18', True, False)
('2022-01-19', True, False)
('2022-01-20', True, False)
('2022-01-21', True, False)
('2022-01-24', True, False)
('2022-01-25', True, False)
('2022-01-26', True, False)
('2022-01-27', True, False)
('2022-01-28', True, False)
('2022-02-03', True, False)
('2022-02-04', True, False)
('2022-02-07', True, False)
('2022-02-08', True,

In [23]:
bt1.update_information()

In [24]:
bt1.JOUNAL

날짜    종목코드    체결단가 체결수량   매매비용 매매구분
0      2018-01-29  108320   53600    3  226.0   매수
1      2018-01-29  178920   42850    3  181.0   매수
2      2018-01-29  097520   17300    3   73.0   매수
3      2018-01-29  036420   66373    3  280.0   매수
4      2018-01-29  003670   47493    3  200.0   매수
...           ...     ...     ...  ...    ...  ...
77616  2018-07-13  000120  170000    3  717.0   매수
77617  2018-07-13  000060   18950    3   80.0   매수
77618  2018-07-13  000050   13850    3   58.0   매수
77619  2018-07-13  000700    6020    3   25.0   매수
77620  2018-07-13  003480    3695    3   16.0   매수

[77621 rows x 6 columns]

In [28]:
bt1.ECONO_INFORM 

날짜      매수총합 매도총합      매매비용 실현손익
0    2018-01-29  94210869  0.0  132393.0  0.0
1    2018-01-30  93977730  0.0  132066.0  0.0
2    2018-01-31  93595980  0.0  131535.0  0.0
3    2018-02-01  93843750  0.0  131874.0  0.0
4    2018-02-02  92752998  0.0  130342.0  0.0
..          ...       ...  ...       ...  ...
107  2018-07-09  85337166  0.0  119920.0  0.0
108  2018-07-10  85255461  0.0  119790.0  0.0
109  2018-07-11  84702360  0.0  119021.0  0.0
110  2018-07-12  85506141  0.0  120166.0  0.0
111  2018-07-13  87842394  0.0  123435.0  0.0

[112 rows x 5 columns]

In [32]:
ut.making_mt_plot(handle_data=df_test1, code='298000', jounal=bt1.JOUNAL)

In [34]:
bt1.ECONO_INFORM[bt1.ECONO_INFORM['실현손익'] > 0.0].shape[0] / bt1.ECONO_INFORM.shape[0]

0.0